# Green and Red Candle Project
## Coded by Victor Zheng & Supervised under Mohammed Hasan

## Progress
##### 4-17-2021: Debugged last index dateTimeMaxHTP for why it was (0,0,0)

In [4]:
import pandas as pd
import numpy as np
import math
#df = pd.read_csv('Jan 2020 - Dec 2020 merged SPY - Copy.csv')
df = pd.read_csv('Even-smaller-dataframe.csv')
df

Date TimeBarStart Ticker CallPut  Strike  ExpirationDate  \
0      20200304   9:30:00 AM    SPY       P   306.5        20200304   
1      20200304   9:30:00 AM    SPY       P   288.0        20200304   
2      20200304   9:30:00 AM    SPY       P   279.0        20200304   
3      20200304   9:30:00 AM    SPY       P   304.5        20200304   
4      20200304   9:30:00 AM    SPY       P   289.0        20200304   
...         ...          ...    ...     ...     ...             ...   
80348  20200311   4:14:00 PM    SPY       C   274.0        20200311   
80349  20200311   4:14:00 PM    SPY       C   271.0        20200311   
80350  20200311   4:14:00 PM    SPY       C   276.0        20200311   
80351  20200311   4:14:00 PM    SPY       C   282.0        20200311   
80352  20200311   4:14:00 PM    SPY       C   280.0        20200311   

       OpenTradePrice  HighTradePrice  LowTradePrice  CloseTradePrice  \
0                2.64            2.76           2.64             2.76   
1                0.04            0.06           0.03             0.03   
2                0.01            0.01           0.01             0.01   
3                1.70            1.70           1.62             1.62   
4                0.03            0.05           0.03             0.05   
...               ...             ...            ...              ...   
80348            1.06            1.11           1.02             1.05   
80349            3.75            3.75           3.75             3.75   
80350            0.27            0.28           0.17             0.25   
80351            0.01            0.01           0.01             0.01   
80352            0.02            0.02           0.02             0.02   

       UnderOpenBidPrice  UnderOpenAskPrice  UnderCloseBidPrice  \
0                 306.05             306.07              305.85   
1                 306.06             306.07              306.19   
2                 305.95             305.97              305.95   
3                 306.15             306.16              306.38   
4                 306.09             306.11              306.17   
...                  ...                ...                 ...   
80348             274.65             274.71              274.62   
80349             274.67             274.71              274.67   
80350             274.70             274.74              274.59   
80351             274.54             274.59              274.54   
80352             274.58             274.64              274.58   

       UnderCloseAskPrice    VWAP  Volume  TotalTrades  
0                  305.87  2.7000       2            2  
1                  306.20  0.0418      11            6  
2                  305.97  0.0100      25            1  
3                  306.40  1.6886       7            2  
4                  306.19  0.0389      36            4  
...                   ...     ...     ...          ...  
80348              274.68  1.0830      23            7  
80349              274.71  3.7500       1            1  
80350              274.60  0.2406      17            8  
80351              274.59  0.0100       3            2  
80352              274.64  0.0200     100            1  

[80353 rows x 17 columns]

## Get minimum value for call/put between 9:46AM and the timecallmax for that day

In [5]:
#function that compares if time 1 is < time 2
def beforeTime(time1,time2):
    
    if len(time1) != 11:
        time1 = "0" + time1
    if len(time2) != 11:
        time2 = "0" + time2
    
    #check last 2 chars to see if AM or PM
    if time1[-2:] == "AM":
        t1IsAM = True
    else:
        t1IsAM = False
    if time2[-2:] == "AM":
        t2IsAM = True
    else:
        t2IsAM = False
    
    if t1IsAM and not t2IsAM:
        return True
    elif t1IsAM and t2IsAM:
        return True if time1 < time2 else False
    elif not t1IsAM and t2IsAM:
        return False
    else: #t1 is pm and t2 is pm
        return True if time1 < time2 else False

#sample test cases - expected TFFF
print(beforeTime("10:05:00 AM","3:59:00 PM"), beforeTime("10:05:00 PM","3:59:00 PM"), beforeTime("10:05:00 AM","3:59:00 AM"),beforeTime("10:05:00 PM","3:59:00 AM"))

True False False False


### Starting price difference - green (increase) and red (decrease) indicators for the first 5 mins of each date

In [6]:
dateTimeCandleSP = [] #(date,time,color,StrikePrice,StockPrice)
date = df.iloc[0]["Date"]
openPrice = df.iloc[0]["UnderOpenAskPrice"]
skipDate = False
#indices: 0=Date, 1=TimeBarStart, 13= UnderCloseAskPrice, 11=UnderOpenAskPrice
for index,row in df.iterrows():
    #we are looking for the UnderOpenAskPrice(UOAP) at 9:30:00 AM (the first time it occurs) 
    #we are looking for the UnderOpenAskPrice (UOAP) at 9:36:00 AM (the last time it occurs)
    #then we subtract the 9:35:00 AM time by the 9:30:00 AM time
    
    if date == row[0]:
        if skipDate:
            continue
        #lastPrice = row["UnderCloseAskPrice"]
        prevRow = row
        #if time is past 9:35AM, then use the latest 9:35AM (if it doesn't exist, then use the current row's time)
        time = row[1]
        if not beforeTime(time,"9:36:00 AM"):
            #calculate starting price difference
            
            #if 9:35 exists
            if prevRow[1] == "9:35:00 AM":
                #we take the UnderCloseAskPrice
                lastPrice = prevRow[13]
            else:
                #if 9:35 doesn't exist
                #if 9:36 exists, then take the open price, otherwise skip this date
                if time == "9:36:00 AM":
                    lastPrice = row[11]
                else:
                    skipDate = True
                    continue
            diff = lastPrice - openPrice
            if math.isnan(diff):
                #either openPrice or lastPrice doesn't exist
                skipDate = True
                continue
            #print("date={},lastPrice={}".format(date,lastPrice))
            if diff >= 0:
                #green start
                dateTimeCandleSP.append((date,time,"GREEN",math.ceil(lastPrice),lastPrice))
            else:
                dateTimeCandleSP.append((date,time,"RED",math.floor(lastPrice),lastPrice))
            skipDate = True
    else:
        #we found new date, get the green/red bar for the previous date, reinitialize some variables
        date = row[0]
        openPrice = row[11]
        skipDate = False

In [7]:
#(date,time,color,StrikePrice,StockPrice)
dateTimeCandleSP

[(20200304, '9:36:00 AM', 'RED', 305, 305.36),
 (20200306, '9:36:00 AM', 'GREEN', 294, 293.8),
 (20200311, '9:36:00 AM', 'GREEN', 282, 281.13)]

In [8]:
dtcspIdx = 0
dfStartIdx = 0
dateWithOTP = [] #(date, time, CallPut, SP, OTP)
for dtcsp in dateTimeCandleSP:
    #print("dateWithOTP: {}".format(dateWithOTP))
    date, time, color, strikeP = dtcsp[0],dtcsp[1],dtcsp[2], dtcsp[3]
    for index,row in df.iloc[dfStartIdx:].iterrows():
        if color == "GREEN":
            #This is call, get OpenTradePrice(OTP) at 9:36AM
            #Match Date, Time, Call=C, StrikePrice
            if row[0] == date and row[1] == time and row[3] == "C" and row[4] == strikeP:
                dateWithOTP.append((date,time,"C",strikeP,row[6]))
                #update for next iteration of dtcsp
                dfStartIdx = index + 1
                break
        else:
            #This is put, get OpenTradePrice(OTP) at 9:36AM
            #Match Date, Time, Call=P, StrikePrice
            if row[0] == date and row[1] == time and row[3] == "P" and row[4] == strikeP:
                dateWithOTP.append((date,time,"P",strikeP,row[6]))
                #update for next iteration of dtcsp
                dfStartIdx = index + 1
                break

#if the candle is green then we want to buy a call
#if call then you look for the UnderOpenAskPrice at 9:36:00 AM and round that up to next whole number, this gets the Call_SP
#then we look for the Call_SP and see what the OpenTradePrice is at 9:36:00 AM


#if the candle is red then we want to buy a put
#if put then you look for the UnderOpenAskPrice at 9:36:00 AM and round that down to next whole number, this gets the Put_SP
#then we look for the Put_SP and see what the OpenTradePrice is at 9:36:00 AM

In [9]:
#(date, time, CallPut, SP, OTP)
print("(date, time,CallPut, SP, OTP)")
dateWithOTP

(date, time,CallPut, SP, OTP)


[(20200304, '9:36:00 AM', 'P', 305, 2.26),
 (20200306, '9:36:00 AM', 'C', 294, 2.87),
 (20200311, '9:36:00 AM', 'C', 282, 3.24)]

#### For each date,SP,CallPut in dateWithOTP, find the maximum of the hightradeprice and time (b/w 9:37:00 AM to 3:59:00 PM

In [27]:
dfStartIdx = 0
#Date	TimeBarStart	Ticker	CallPut	Strike	ExpirationDate	OpenTradePrice	HighTradePrice	LowTradePrice	CloseTradePrice	
dateTimeMaxHTP = [(0,0,0) for _ in range(len(dateWithOTP))] #[date,time,maxHTP]
prevDate = dateWithOTP[0][0]
N = len(df)
curDfLen = N
for dOTPidx, (date,_,CallPut,sp,_) in enumerate(dateWithOTP):
    print("Checking for date={},CallPut={},sp={}".format(date,CallPut,sp))
    maxHTP = -1
    doSameDate = False
    for index,row in df.iloc[dfStartIdx:].iterrows():
        print("index,dfStartIdx,N-dfStartIdx-1: {},{},{}".format(index,dfStartIdx,N-dfStartIdx-1))
        print("htp={},maxHTP={},time={}".format(row[7],maxHTP,row[1]))
        if index == N-1: #index == N - dfStartIdx - 2:
                print("if4.1-----------------------------------------")
                #case 1 - we're done with prev date
                dateTimeMaxHTP[dOTPidx] = (prevDate,maxHTPTime,maxHTP)
            
                #initialize variables for next iteration of dateWithOTP
                dfStartIdx = index + 1
                prevDate = row[0]
                maxHTP = -1
                break
        elif date == row[0] and CallPut == row[3] and sp == row[4]:
            print("if1")
            print("row: {}".format(list(row)))
            #Check if there's a new max HTP
            #print("htp={},maxHTP={},time={}".format(row[7],maxHTP,row[1]))
            if row[7] > maxHTP:
                print("if2")
                print("update for maxHTP: {}".format(row[7]))
                maxHTP = row[7]
                maxHTPTime = row[1]
        elif date != row[0]:
            print("if3")
            #date doesn't match, so we're done searching for previous date OR this date has no value in df
            if maxHTP != -1: #or index == N - dfStartIdx - 1: #the right of "or" represents last index, so we compute dateTimeMaxHTP  
                print("if4")
                #case 1 - we're done with prev date
                dateTimeMaxHTP[dOTPidx] = (prevDate,maxHTPTime,maxHTP)
            
                #initialize variables for next iteration of dateWithOTP
                dfStartIdx = index + 1
                prevDate = row[0]
                maxHTP = -1
                break
            elif index == N-1: #index == N - dfStartIdx - 2:
                print("if4.1-----------------------------------------")
                #case 1 - we're done with prev date
                dateTimeMaxHTP[dOTPidx] = (prevDate,maxHTPTime,maxHTP)
            
                #initialize variables for next iteration of dateWithOTP
                dfStartIdx = index + 1
                prevDate = row[0]
                maxHTP = -1
                break
            else:
                print('if5')
                #Case 2 - date has no value in df, so doesn't exist in dateWithOTP
                #keep iterating until we past this date and until we found the date that matches dateWithOTP
                dfStartIdx = index + 1
                print("dfStartIdx: {}".format(dfStartIdx))
                for indexb,rowb in df.iloc[dfStartIdx:].iterrows():
                    if rowb[0] == date:
                        print("if6")
                        prevDate = rowb[0]
                        dfStartIdx = indexb
                        doSameDate = True #found matching date so now iterate from that as startIdx to cover it instead of using current for loop
                        break
                if doSameDate:
                    print("if7")
                    break
            

    if doSameDate:
        print("if7.2")
        for index,row in df.iloc[dfStartIdx:].iterrows():
            print("index,dfStartIdx,N-dfStartIdx-1: {},{},{}".format(index,dfStartIdx,N-dfStartIdx-1))
            if index == N-1: #N - dfStartIdx - 2: # 80352 - 41175 # - 1
                print("if11")
                #reached the last index in df, so update for maxHTP
                #case 1 - we're done with prev date
                dateTimeMaxHTP[dOTPidx] = (prevDate,maxHTPTime,maxHTP)

                #initialize variables for next iteration of dateWithOTP
                dfStartIdx = index + 1
                prevDate = row[0]
                maxHTP = -1
                break
            elif date == row[0] and CallPut == row[3] and sp == row[4]:
                print("if8")
                print("row: {}".format(list(row)))
                #Check if there's a new max HTP
                print("htp={},maxHTP={},time={}".format(row[7],maxHTP,row[1]))
                if row[7] > maxHTP:
                    print("if9")
                    print("update for maxHTP: {}".format(row[7]))
                    maxHTP = row[7]
                    maxHTPTime = row[1]
            elif date != row[0]:
                #date doesn't match, so we're done searching for previous date OR this date has no value in df
                print("if10")
                if maxHTP != -1: #or index == N - dfStartIdx - 1: #the right of "or" represents last index, so we compute dateTimeMaxHTP 
                    #case 1 - we're done with prev date
                    dateTimeMaxHTP[dOTPidx] = (prevDate,maxHTPTime,maxHTP)

                    #initialize variables for next iteration of dateWithOTP
                    dfStartIdx = index + 1
                    prevDate = row[0]
                    maxHTP = -1
                    break
            

Checking for date=20200304,CallPut=P,sp=305
index,dfStartIdx,N-dfStartIdx-1: 0,0,80352
htp=2.76,maxHTP=-1,time=9:30:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1,0,80352
htp=0.06,maxHTP=-1,time=9:30:00 AM
index,dfStartIdx,N-dfStartIdx-1: 2,0,80352
htp=0.01,maxHTP=-1,time=9:30:00 AM
index,dfStartIdx,N-dfStartIdx-1: 3,0,80352
htp=1.7,maxHTP=-1,time=9:30:00 AM
index,dfStartIdx,N-dfStartIdx-1: 4,0,80352
htp=0.05,maxHTP=-1,time=9:30:00 AM
index,dfStartIdx,N-dfStartIdx-1: 5,0,80352
htp=0.01,maxHTP=-1,time=9:30:00 AM
index,dfStartIdx,N-dfStartIdx-1: 6,0,80352
htp=13.96,maxHTP=-1,time=9:30:00 AM
index,dfStartIdx,N-dfStartIdx-1: 7,0,80352
htp=0.56,maxHTP=-1,time=9:30:00 AM
index,dfStartIdx,N-dfStartIdx-1: 8,0,80352
htp=3.84,maxHTP=-1,time=9:30:00 AM
index,dfStartIdx,N-dfStartIdx-1: 9,0,80352
htp=0.03,maxHTP=-1,time=9:30:00 AM
index,dfStartIdx,N-dfStartIdx-1: 10,0,80352
htp=2.11,maxHTP=-1,time=9:30:00 AM
if1
row: [20200304, '9:30:00 AM', 'SPY', 'P', 305.0, 20200304, 2.0, 2.11, 1.81, 1.81, 306.06, 306

htp=0.08,maxHTP=3.09,time=9:39:00 AM
index,dfStartIdx,N-dfStartIdx-1: 742,0,80352
htp=2.67,maxHTP=3.09,time=9:39:00 AM
index,dfStartIdx,N-dfStartIdx-1: 743,0,80352
htp=0.1,maxHTP=3.09,time=9:39:00 AM
index,dfStartIdx,N-dfStartIdx-1: 744,0,80352
htp=0.92,maxHTP=3.09,time=9:39:00 AM
index,dfStartIdx,N-dfStartIdx-1: 745,0,80352
htp=0.04,maxHTP=3.09,time=9:39:00 AM
index,dfStartIdx,N-dfStartIdx-1: 746,0,80352
htp=2.93,maxHTP=3.09,time=9:39:00 AM
if1
row: [20200304, '9:39:00 AM', 'SPY', 'P', 305.0, 20200304, 2.93, 2.93, 2.55, 2.59, 304.21, 304.23, 304.87, 304.88, 2.7633, 336, 49]
index,dfStartIdx,N-dfStartIdx-1: 747,0,80352
htp=0.03,maxHTP=3.09,time=9:39:00 AM
index,dfStartIdx,N-dfStartIdx-1: 748,0,80352
htp=6.66,maxHTP=3.09,time=9:39:00 AM
index,dfStartIdx,N-dfStartIdx-1: 749,0,80352
htp=0.26,maxHTP=3.09,time=9:39:00 AM
index,dfStartIdx,N-dfStartIdx-1: 750,0,80352
htp=0.19,maxHTP=3.09,time=9:39:00 AM
index,dfStartIdx,N-dfStartIdx-1: 751,0,80352
htp=5.38,maxHTP=3.09,time=9:39:00 AM
index,df

htp=3.96,maxHTP=3.09,time=9:46:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1268,0,80352
htp=0.08,maxHTP=3.09,time=9:46:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1269,0,80352
htp=3.58,maxHTP=3.09,time=9:46:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1270,0,80352
htp=1.29,maxHTP=3.09,time=9:46:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1271,0,80352
htp=3.26,maxHTP=3.09,time=9:46:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1272,0,80352
htp=3.25,maxHTP=3.09,time=9:47:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1273,0,80352
htp=0.06,maxHTP=3.09,time=9:47:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1274,0,80352
htp=2.33,maxHTP=3.09,time=9:47:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1275,0,80352
htp=0.06,maxHTP=3.09,time=9:47:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1276,0,80352
htp=0.79,maxHTP=3.09,time=9:47:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1277,0,80352
htp=0.04,maxHTP=3.09,time=9:47:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1278,0,80352
htp=2.55,maxHTP=3.09,time=9:47:00 AM
if1
row: [20200304, '9:47:00 AM', 'SPY', 'P', 305.

index,dfStartIdx,N-dfStartIdx-1: 1869,0,80352
htp=2.09,maxHTP=3.33,time=9:56:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1870,0,80352
htp=0.01,maxHTP=3.33,time=9:56:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1871,0,80352
htp=2.6,maxHTP=3.33,time=9:56:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1872,0,80352
htp=0.51,maxHTP=3.33,time=9:56:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1873,0,80352
htp=0.96,maxHTP=3.33,time=9:56:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1874,0,80352
htp=1.65,maxHTP=3.33,time=9:56:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1875,0,80352
htp=0.64,maxHTP=3.33,time=9:56:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1876,0,80352
htp=2.84,maxHTP=3.33,time=9:56:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1877,0,80352
htp=0.69,maxHTP=3.33,time=9:56:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1878,0,80352
htp=0.03,maxHTP=3.33,time=9:56:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1879,0,80352
htp=2.01,maxHTP=3.33,time=9:56:00 AM
index,dfStartIdx,N-dfStartIdx-1: 1880,0,80352
htp=2.25,maxHTP=3.33,time=9:56:00 AM
index

htp=0.05,maxHTP=3.52,time=10:08:00 AM
index,dfStartIdx,N-dfStartIdx-1: 2636,0,80352
htp=0.57,maxHTP=3.52,time=10:08:00 AM
index,dfStartIdx,N-dfStartIdx-1: 2637,0,80352
htp=1.34,maxHTP=3.52,time=10:08:00 AM
index,dfStartIdx,N-dfStartIdx-1: 2638,0,80352
htp=1.9,maxHTP=3.52,time=10:08:00 AM
index,dfStartIdx,N-dfStartIdx-1: 2639,0,80352
htp=1.55,maxHTP=3.52,time=10:08:00 AM
index,dfStartIdx,N-dfStartIdx-1: 2640,0,80352
htp=6.0,maxHTP=3.52,time=10:08:00 AM
index,dfStartIdx,N-dfStartIdx-1: 2641,0,80352
htp=1.62,maxHTP=3.52,time=10:08:00 AM
index,dfStartIdx,N-dfStartIdx-1: 2642,0,80352
htp=1.95,maxHTP=3.52,time=10:08:00 AM
index,dfStartIdx,N-dfStartIdx-1: 2643,0,80352
htp=0.38,maxHTP=3.52,time=10:08:00 AM
index,dfStartIdx,N-dfStartIdx-1: 2644,0,80352
htp=0.66,maxHTP=3.52,time=10:08:00 AM
index,dfStartIdx,N-dfStartIdx-1: 2645,0,80352
htp=1.31,maxHTP=3.52,time=10:08:00 AM
index,dfStartIdx,N-dfStartIdx-1: 2646,0,80352
htp=0.47,maxHTP=3.52,time=10:08:00 AM
index,dfStartIdx,N-dfStartIdx-1: 2647,0,

...

htp=0.34,maxHTP=3.5,time=2:12:00 PM
index,dfStartIdx,N-dfStartIdx-1: 75002,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 75003,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 75004,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 75005,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 75006,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 75007,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 75008,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 75009,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 75010,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 75011,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 75012,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 75013,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 75014,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 75015,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 75016,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 75017,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 75018,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 75019,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 75020,61645,1

index,dfStartIdx,N-dfStartIdx-1: 76054,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 76055,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 76056,61645,18707
if8
row: [20200311, '2:36:00 PM', 'SPY', 'C', 282.0, 20200311, 0.28, 0.28, 0.24, 0.24, 274.62, 274.64, 274.06, 274.07, 0.255, 16, 5]
htp=0.28,maxHTP=3.5,time=2:36:00 PM
index,dfStartIdx,N-dfStartIdx-1: 76057,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 76058,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 76059,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 76060,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 76061,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 76062,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 76063,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 76064,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 76065,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 76066,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 76067,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 76068,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 76069,61645,18707
index,dfStartId

index,dfStartIdx,N-dfStartIdx-1: 77203,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 77204,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 77205,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 77206,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 77207,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 77208,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 77209,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 77210,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 77211,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 77212,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 77213,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 77214,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 77215,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 77216,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 77217,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 77218,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 77219,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 77220,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 77221,61645,18707
index,dfStartIdx,N-dfStartIdx-1

htp=0.06,maxHTP=3.5,time=3:26:00 PM
index,dfStartIdx,N-dfStartIdx-1: 78322,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 78323,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 78324,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 78325,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 78326,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 78327,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 78328,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 78329,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 78330,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 78331,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 78332,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 78333,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 78334,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 78335,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 78336,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 78337,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 78338,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 78339,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 78340,61645,1

index,dfStartIdx,N-dfStartIdx-1: 79511,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 79512,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 79513,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 79514,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 79515,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 79516,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 79517,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 79518,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 79519,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 79520,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 79521,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 79522,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 79523,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 79524,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 79525,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 79526,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 79527,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 79528,61645,18707
index,dfStartIdx,N-dfStartIdx-1: 79529,61645,18707
index,dfStartIdx,N-dfStartIdx-1

In [28]:
dateTimeMaxHTP

[(20200304, '9:58:00 AM', 3.52),
 (20200306, '10:51:00 AM', 5.15),
 (20200311, '9:36:00 AM', 3.5)]

In [12]:
(done)#fix the last date needs to have values - something wrong with checking last element in df, we broke out without appending
#get the right time frame

In [17]:
N

80353